In [2]:
import xlsxwriter

In [39]:
from repytex.worksheets.worksheet import pull_datas
import pandas as pd
import numpy as np
import sqlite3

In [4]:
conn = sqlite3.connect('./recopytex.db')

In [7]:
datas = pull_datas(1, conn)
datas

{'evaluation':    id               name  term  t_id
 0   1  DS1 mise en jambe     1     1,
 'exercises':    id                        name  eval_id                        date comment
 0   1  1 - Prendre la température        1  2017-09-05 00:00:00.000000        
 1   2             2 - Maladroite!        1  2017-09-05 00:00:00.000000        ,
 'question_scores':       id  question_id  student_id value
 0      1            1           1     1
 1      2            2           1     2
 2      3            3           1     .
 3      4            1           2     2
 4      5            2           2     2
 5      6            3           2     1
 6      7            1           3     3
 7      8            2           3     0
 8      9            3           3     0
 9     10            1           4     3
 10    11            2           4     3
 11    12            3           4     0
 12    13            1           5     1
 13    14            2           5     2
 14    15            

In [11]:
datas['evaluation']["name"][0]

'DS1 mise en jambe'

In [64]:
q_df = datas["questions"]
q_df = q_df.assign(
    Nom = q_df[["name", "comment"]].apply(lambda x: " ".join(x), 1)
)

In [65]:
q_df.head()

id name  score_rate  is_leveled  exercise_id competence       domain  \
0   1    1           0           1            1       Cher    Grandeurs   
1   2    2           0           1            1        Cal    Grandeurs   
2   3  2.c           0           1            1        Cal    Grandeurs   
0   4                0           1            2       Cher  4opérations   
1   5                0           1            2       Cher  4opérations   

                             comment                                    Nom  
0             Lecture du thermomètre               1 Lecture du thermomètre  
1        Suivre programme de calculs          2 Suivre programme de calculs  
2  Renverser un programme de calculs  2.c Renverser un programme de calculs  
0    Lire le tableau et le graphique        Lire le tableau et le graphique  
1             Décomposer le problème                 Décomposer le problème

In [66]:
datas["exercises"]

id                        name  eval_id                        date comment
0   1  1 - Prendre la température        1  2017-09-05 00:00:00.000000        
1   2             2 - Maladroite!        1  2017-09-05 00:00:00.000000

In [70]:
ex_q = q_df.groupby("exercise_id")\
    .agg({"score_rate": np.sum, "competence": lambda x: '-'.join(list(x))}) \
    .merge(datas["exercises"], left_index=True, right_on='id')
ex_q = ex_q.assign(
    Nom = ex_q["name"].apply(lambda x: f"Ex {x}"),
    exercise_id = ex_q["id"]
)
ex_q

score_rate             competence  id                        name  eval_id  \
0           0           Cher-Cal-Cal   1  1 - Prendre la température        1   
1           0  Cher-Cher-Rai-Cal-Com   2             2 - Maladroite!        1   

                         date comment                            Nom  \
0  2017-09-05 00:00:00.000000          Ex 1 - Prendre la température   
1  2017-09-05 00:00:00.000000                     Ex 2 - Maladroite!   

   exercise_id  
0            1  
1            2

In [85]:
sel_fields = ['Nom', 'competence', 'score_rate', 'exercise_id']
xls_df = pd.concat([ex_q[sel_fields], q_df[sel_fields]]).sort_values("exercise_id")
xls_df

Nom             competence  score_rate  \
0          Ex 1 - Prendre la température           Cher-Cal-Cal           0   
0               1 Lecture du thermomètre                   Cher           0   
1          2 Suivre programme de calculs                    Cal           0   
2  2.c Renverser un programme de calculs                    Cal           0   
1                     Ex 2 - Maladroite!  Cher-Cher-Rai-Cal-Com           0   
0        Lire le tableau et le graphique                   Cher           0   
1                 Décomposer le problème                   Cher           0   
2                Manipuler les grandeurs                    Rai           0   
3               Mener à bien les calculs                    Cal           0   
4                              Rédaction                    Com           0   

   exercise_id  
0            1  
0            1  
1            1  
2            1  
1            2  
0            2  
1            2  
2            2  
3            2  
4            2

In [86]:
writer = pd.ExcelWriter("./test.xlsx", engine="xlsxwriter")
xls_df.to_excel(writer, index=False, sheet_name='DNB blanc 2')

In [87]:
workbook = writer.book
worksheet = writer.sheets['DNB blanc 2']

In [91]:
first_line_format = workbook.add_format({"align": 'center', "rotation":90})

worksheet.set_column('A:D', 20)


0

In [89]:
writer.save()

## Fait au DNB blanc 1

In [9]:
wb = xlsxwriter.Workbook("DNB_BLANC_pro1.xlsx")

Formatages

In [10]:
eval_format = wb.add_format({'bold': True, 'font_color': 'red'})
eval_cell = wb.add_format()
eval_cell.set_bg_color("red")
# exo_cell

La feuille de calcul

In [11]:
wb = xlsxwriter.Workbook("DS4_302.xlsx")

In [12]:
ws = wb.add_worksheet()

En tête du tableau

In [13]:
ws.write(0,1,"Competence")
ws.write(0,2,"Barème")

0

Toutes les questions et exercices

In [14]:
def q_line(q, row, ws):
    ws.write(row, 0, f"{q.name} - {q.comment}")
    ws.write(row, 1, f"{q.competence}")
    ws.write(row, 2, q.score_rate)

In [15]:
def exo_block(exo, row, ws):
    qrow = row
    for q in exo["questions"]:
        qrow += 1
        q_line(q, qrow, ws)
    ws.write(row, 0, f"Ex {exo['name']}")
    row_range = ", ".join([f"C{i}" for i in range(row+2, qrow+2)])
    for i in range(30):
        ws.write(row, i+2, f"=SUM({row_range})")
    return qrow

In [16]:
row = 2
exo_rows = []
for exo in ev.exercises:
    exo_rows.append(row)
    row = exo_block(exo, row, ws) + 1
ws.write(1,0, ev.name, eval_format)
exo_xls_range = ", ".join([f"C{i+1}" for i in exo_rows])
for i in range(30):
    ws.write(1,i+2, f"=SUM({exo_xls_range})", eval_format)

In [17]:
wb.close()

# Avec openpyxl

In [13]:
from openpyxl import Workbook
from openpyxl.styles import PatternFill, Border, Side, Alignment, Protection, Font, colors

In [14]:
colors.RED

'00FF0000'

In [15]:
wb = Workbook()

In [16]:
ws = wb.create_sheet(ev.name)

In [17]:
ws.cell(1,2,"Competence")
ws.cell(1,3,"Barème")

<Cell 'DNB blanc1'.C1>

In [18]:
def q_line(q, row, ws):
    ws.cell(row, 1, f"{q.name} - {q.comment}")
    ws.cell(row, 2, f"{q.competence}")
    ws.cell(row, 3, q.score_rate)

In [19]:
def exo_block(exo, row, ws):
    qrow = row
    for q in exo["questions"]:
        qrow += 1
        q_line(q, qrow, ws)
    ws.cell(row, 1, f"Ex {exo['name']}")
    row_range = ", ".join([f"C{i}" for i in range(row+1, qrow+1)])
    ws.cell(row, 3, f"=SUM({row_range})")
    return qrow

In [20]:
row = 3
exo_rows = []
for exo in ev.exercises:
    exo_rows.append(row)
    row = exo_block(exo, row, ws) + 1
eval_row = ws.row_dimensions[2]
eval_row.fill = PatternFill(bgColor=colors.RED)
ws.cell(2,1, ev.name)
exo_xls_range = ", ".join([f"C{i}" for i in exo_rows])
ws.cell(2,3, f"=SUM({exo_xls_range})")

<Cell 'DNB blanc1'.C2>

In [21]:
ev.tribe

'302'

In [22]:
wb.save(f"./{ev.name}-{ev.tribe}.xlsx")